In [9]:
import pickle
from igraph import *

with open("./all_subgraphs_all_e3.pkl", "rb") as f:
    dt = pickle.load(f)

display(len(dt))

413462

In [10]:
dt[0]

(False, (<igraph.Graph at 0x7fa5805075e0>, '411764'))

In [11]:
import os
import pickle
from mapping import *

In [12]:
global_data = []

focus_index = 0
flag_focus = 0
maptype = True

for i in range(len(dt)):
    print("\r# processing {}/{}".format(i, len(dt)), end="")
    p = dt[i]
    dlabel, (dgraph, dtarget) = p
    slice_corpus = []
    slicefile_corpus = []
    slicefile_labels = []
    slicefile_focus = []
    slicefile_func = []
    slicefile_filenames = []
    graph_corpus = []

    for sentence in dgraph.vs["code"]:
        
        
        start = str.find(sentence,r'printf("')
        if start != -1:
            start = str.find(sentence,r'");')
            sentence = sentence[:start + 2]
        
        fm = str.find(sentence,'/*')
        if fm != -1:
            sentence = sentence[:fm]
        else:
            fm = str.find(sentence,'//')
            if fm != -1:
                sentence = sentence[:fm]

        sentence = sentence.strip() + " "

        list_tokens = create_tokens(sentence)
        
        if flag_focus == 0:
            focus_index = focus_index + len(list_tokens)

        if maptype:

            slice_corpus.append(list_tokens)
        else:
            slice_corpus = slice_corpus + list_tokens
    
    
    if maptype:
        slice_corpus, slice_func = mapping(slice_corpus)
        slice_func = list(set(slice_func))
        if slice_func == []:
            slice_func = ['main']
        sample_corpus = []
        for sentence in slice_corpus:
            list_tokens = create_tokens(sentence + " ")
            sample_corpus = sample_corpus + list_tokens
            graph_corpus.append(list_tokens)
        slicefile_corpus.append(sample_corpus)
        slicefile_func.append(slice_func)
    else:
        slicefile_corpus.append(slice_corpus)

    global_data.append((dlabel, dgraph, dtarget, graph_corpus))

# processing 413461/413462

In [13]:
writer = open("./all_subgraphs_all_tokenize.pkl", "wb")
pickle.dump(global_data, writer)

In [1]:
import pickle
import os
reader = open("./all_subgraphs_all_tokenize.pkl", "rb")
global_data = pickle.load(reader)

In [2]:
# tokens and node length counter
tmp_tokens = []
tmp_lengths = []
for node in global_data:
    codes = node[3]
    for token_list in codes:
        tmp_tokens.extend(token_list)
        tmp_lengths.append(len(token_list))

In [3]:
from collections import Counter
counter_tokens = Counter(tmp_tokens)
counter_lengths = Counter(tmp_lengths)

In [4]:
token_dict = []
for token, count in counter_tokens.items():
    if count > 2 and "CWE" not in token:
        token_dict.append(token)

In [5]:
print(len(token_dict))

2638


In [6]:
print(len(counter_tokens))

3105


In [7]:
token_set = set(token_dict)

In [8]:
for node in global_data:
    codes = node[3]
    for token_list in codes:
        for i in range(len(token_list)):
            if token_list[i] not in token_set:
                token_list[i] = "<UNK>"

In [9]:
global_data[0][3]

[['variable_0',
  '=',
  'func_0',
  '(',
  '"',
  'SMI',
  'Paths',
  '"',
  ',',
  'sizeof',
  '(',
  'variable_1',
  ')',
  ',',
  '"',
  '<UNK>',
  '"',
  ',',
  '0',
  ',',
  '(',
  '(',
  'void',
  '*',
  ')',
  '(',
  '&',
  'variable_2',
  ')',
  ')',
  ',',
  '&',
  'variable_3',
  ',',
  '"',
  'General',
  '"',
  ',',
  '"',
  '<UNK>',
  '"',
  ',',
  'variable_4',
  ',',
  '(',
  '(',
  'void',
  '*',
  ')',
  '0',
  ')',
  ',',
  'variable_5',
  ',',
  'variable_6',
  ',',
  'variable_7',
  ')'],
 ['static',
  'uat_field_t',
  'variable_7',
  '[',
  ']',
  '=',
  '{',
  '{',
  '(',
  '"',
  'name',
  '"',
  ')',
  ',',
  '(',
  '"',
  '<UNK>',
  'path',
  '"',
  ')',
  ',',
  '(',
  'variable_8',
  ')',
  ',',
  '{',
  '(',
  'variable_9',
  ')',
  ',',
  '(',
  'variable_10',
  ')',
  ',',
  '(',
  'variable_11',
  ')',
  '}',
  ',',
  '{',
  '(',
  '0',
  ')',
  ',',
  '(',
  '0',
  ')',
  ',',
  '(',
  '0',
  ')',
  '}',
  ',',
  '(',
  '0',
  ')',
  ',',
  '(',
  '"',


In [10]:
corpus = []
for instance in global_data:
    tokens = instance[3]
    corpus.extend(tokens)

In [11]:
len(corpus)
corpus[12500]

['char', '*', 'variable_2', '[', '5', ']', ';']

In [12]:
from gensim.models import fasttext
from gensim.models import word2vec
import pandas as pd
import logging
import random

In [13]:
from gensim.models import Word2Vec, FastText

# model = word2vec.Word2Vec(corpus, min_count=1, iter=10, size=16)
# model.save("word2vec_tokens_unk_min_2.model")
model = Word2Vec.load("word2vec_tokens_unk_min_2.model")
token_dict = model.wv.vocab

In [14]:
model.wv[]

SyntaxError: invalid syntax (<ipython-input-14-a0a93adbd7f4>, line 1)

In [ ]:
model.wv.most_similar("memset")

In [ ]:
list(model.wv["SMI"])

In [ ]:
MAX_CODE_LEN = 120
SIZE = 16

In [ ]:
MAX_CODE_LEN

# Label Formal Fix

In [15]:
# load label xml files
from xml.dom.minidom import parse
dom = parse("SARD_testcaseinfo.xml")


In [16]:
def format_key(path):
    path_segs = path.split("/")
    seg1 = int(path_segs[1])
    seg2 = path_segs[2]
    file_name = path_segs[3]
    
    return str(seg1) + str(seg2) + "/" + file_name

In [17]:
data = dom.documentElement
files = data.getElementsByTagName('file')
label_dict = {}

In [18]:
for file in files:
    file_path = file.getAttribute('path')
    try:
        file_key = format_key(file_path)
    except:
        # print(file_path)
        continue
    flaw_lines = []
    flaws = file.getElementsByTagName('flaw')
    for flaw in flaws:
        flaw_lines.append(int(flaw.getAttribute('line')))
        if flaw_lines != []:
            print(flaw_lines)
    mixeds = file.getElementsByTagName('mixed')
    for mixed in mixeds:
        flaw_lines.append(int(mixed.getAttribute('line')))
    label_dict[file_key] = flaw_lines

[6]
[11]
[15]
[15, 12]
[3]
[0]
[5]
[5]
[4]
[6]
[11]
[11, 10]
[11, 10, 0]
[11, 10, 0, 9]
[19]
[19, 0]
[19, 0, 18]
[0]
[32]
[32, 31]
[32, 31, 31]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]
[0]


[343, 344, 345]
[343, 344, 345, 346]
[924]
[924, 925]
[924, 925, 926]
[924, 925, 926, 923]
[539]
[539, 540]
[539, 540, 542]
[539, 540, 542, 541]
[539, 540, 542, 541, 543]
[539, 540, 542, 541, 543, 544]
[539, 540, 542, 541, 543, 544, 545]
[309]
[309, 310]
[309, 310, 312]
[309, 310, 312, 311]
[4072]
[4072, 4073]
[4072, 4073, 4074]
[460]
[460, 462]
[460, 462, 458]
[460, 462, 458, 459]
[460, 462, 458, 459, 461]
[460, 462, 458, 459, 461, 463]
[1171]
[1171, 1172]
[1171, 1172, 1173]
[1171, 1172, 1173, 1174]
[1171, 1172, 1173, 1174, 1179]
[1171, 1172, 1173, 1174, 1179, 1175]
[1171, 1172, 1173, 1174, 1179, 1175, 1176]
[1171, 1172, 1173, 1174, 1179, 1175, 1176, 1177]
[1171, 1172, 1173, 1174, 1179, 1175, 1176, 1177, 1178]
[1171, 1172, 1173, 1174, 1179, 1175, 1176, 1177, 1178, 1180]
[309]
[309, 310]
[309, 310, 311]
[1340]
[1340, 1342]
[1340, 1342, 1339]
[1340, 1342, 1339, 1341]
[410]
[410, 408]
[410, 408, 409]
[489]
[489, 490]
[489, 490, 491]
[489, 490, 491, 492]
[215]
[215, 216]
[215, 216, 217]
[

[190, 195, 189, 191, 192, 193]
[190, 195, 189, 191, 192, 193, 194]
[217]
[217, 219]
[217, 219, 220]
[217, 219, 220, 222]
[217, 219, 220, 222, 218]
[217, 219, 220, 222, 218, 221]
[219]
[219, 220]
[219, 220, 221]
[219, 220, 221, 217]
[219, 220, 221, 217, 218]
[219, 220, 221, 217, 218, 222]
[180]
[180, 183]
[180, 183, 185]
[180, 183, 185, 186]
[180, 183, 185, 186, 187]
[180, 183, 185, 186, 187, 189]
[180, 183, 185, 186, 187, 189, 181]
[180, 183, 185, 186, 187, 189, 181, 182]
[180, 183, 185, 186, 187, 189, 181, 182, 184]
[180, 183, 185, 186, 187, 189, 181, 182, 184, 188]
[180, 183, 185, 186, 187, 189, 181, 182, 184, 188, 190]
[227]
[227, 228]
[227, 228, 229]
[227, 228, 229, 230]
[682]
[682, 684]
[682, 684, 685]
[682, 684, 685, 687]
[682, 684, 685, 687, 688]
[682, 684, 685, 687, 688, 689]
[682, 684, 685, 687, 688, 689, 692]
[682, 684, 685, 687, 688, 689, 692, 683]
[682, 684, 685, 687, 688, 689, 692, 683, 686]
[682, 684, 685, 687, 688, 689, 692, 683, 686, 690]
[682, 684, 685, 687, 688, 689, 

[206, 207, 208]
[206, 207, 208, 209]
[206, 207, 208, 209, 203]
[206, 207, 208, 209, 203, 204]
[206, 207, 208, 209, 203, 204, 205]
[201]
[201, 204]
[201, 204, 200]
[201, 204, 200, 202]
[201, 204, 200, 202, 203]
[160]
[160, 161]
[160, 161, 163]
[160, 161, 163, 165]
[160, 161, 163, 165, 166]
[160, 161, 163, 165, 166, 167]
[160, 161, 163, 165, 166, 167, 157]
[160, 161, 163, 165, 166, 167, 157, 158]
[160, 161, 163, 165, 166, 167, 157, 158, 159]
[160, 161, 163, 165, 166, 167, 157, 158, 159, 162]
[160, 161, 163, 165, 166, 167, 157, 158, 159, 162, 164]
[212]
[212, 215]
[212, 215, 211]
[212, 215, 211, 213]
[212, 215, 211, 213, 214]
[4072]
[4072, 4067]
[4072, 4067, 4068]
[4072, 4067, 4068, 4069]
[4072, 4067, 4068, 4069, 4070]
[4072, 4067, 4068, 4069, 4070, 4071]
[1155]
[1155, 1153]
[1155, 1153, 1154]
[1155, 1153, 1154, 1156]
[1155, 1153, 1154, 1156, 1157]
[1155, 1153, 1154, 1156, 1157, 1158]
[4848]
[4848, 4849]
[4848, 4849, 4850]
[4848, 4849, 4850, 4852]
[4848, 4849, 4850, 4852, 4854]
[4848, 484

[207, 211, 212, 203, 204, 205, 206, 208, 209, 210]
[207, 211, 212, 203, 204, 205, 206, 208, 209, 210, 213]
[4835]
[4835, 4838]
[4835, 4838, 4841]
[4835, 4838, 4841, 4842]
[4835, 4838, 4841, 4842, 4845]
[4835, 4838, 4841, 4842, 4845, 4834]
[4835, 4838, 4841, 4842, 4845, 4834, 4836]
[4835, 4838, 4841, 4842, 4845, 4834, 4836, 4837]
[4835, 4838, 4841, 4842, 4845, 4834, 4836, 4837, 4839]
[4835, 4838, 4841, 4842, 4845, 4834, 4836, 4837, 4839, 4840]
[4835, 4838, 4841, 4842, 4845, 4834, 4836, 4837, 4839, 4840, 4843]
[4835, 4838, 4841, 4842, 4845, 4834, 4836, 4837, 4839, 4840, 4843, 4844]
[234]
[234, 235]
[234, 235, 236]
[234, 235, 236, 237]
[220]
[220, 219]
[187]
[187, 188]
[187, 188, 185]
[187, 188, 185, 186]
[696]
[696, 699]
[696, 699, 694]
[696, 699, 694, 695]
[696, 699, 694, 695, 697]
[696, 699, 694, 695, 697, 698]
[194]
[194, 196]
[194, 196, 197]
[194, 196, 197, 199]
[194, 196, 197, 199, 201]
[194, 196, 197, 199, 201, 191]
[194, 196, 197, 199, 201, 191, 192]
[194, 196, 197, 199, 201, 191,

...

[479, 480, 484, 486, 487, 488, 490, 493, 494, 495, 497, 500, 501, 502, 504, 506, 507, 477, 478, 481, 482, 483, 485, 489, 491, 492]
[479, 480, 484, 486, 487, 488, 490, 493, 494, 495, 497, 500, 501, 502, 504, 506, 507, 477, 478, 481, 482, 483, 485, 489, 491, 492, 496]
[479, 480, 484, 486, 487, 488, 490, 493, 494, 495, 497, 500, 501, 502, 504, 506, 507, 477, 478, 481, 482, 483, 485, 489, 491, 492, 496, 498]
[479, 480, 484, 486, 487, 488, 490, 493, 494, 495, 497, 500, 501, 502, 504, 506, 507, 477, 478, 481, 482, 483, 485, 489, 491, 492, 496, 498, 499]
[479, 480, 484, 486, 487, 488, 490, 493, 494, 495, 497, 500, 501, 502, 504, 506, 507, 477, 478, 481, 482, 483, 485, 489, 491, 492, 496, 498, 499, 503]
[479, 480, 484, 486, 487, 488, 490, 493, 494, 495, 497, 500, 501, 502, 504, 506, 507, 477, 478, 481, 482, 483, 485, 489, 491, 492, 496, 498, 499, 503, 505]
[479, 480, 484, 486, 487, 488, 490, 493, 494, 495, 497, 500, 501, 502, 504, 506, 507, 477, 478, 481, 482, 483, 485, 489, 491, 492, 496, 498

[588, 593, 594, 587, 589, 590, 591, 592, 595]
[452]
[452, 453]
[452, 453, 454]
[4758]
[4758, 4759]
[4758, 4759, 4760]
[4758, 4759, 4760, 4762]
[4758, 4759, 4760, 4762, 4764]
[4758, 4759, 4760, 4762, 4764, 4757]
[4758, 4759, 4760, 4762, 4764, 4757, 4761]
[4758, 4759, 4760, 4762, 4764, 4757, 4761, 4763]
[179]
[179, 180]
[179, 180, 181]
[179, 180, 181, 182]
[179, 180, 181, 182, 183]
[590]
[590, 592]
[590, 592, 594]
[590, 592, 594, 596]
[590, 592, 594, 596, 597]
[590, 592, 594, 596, 597, 591]
[590, 592, 594, 596, 597, 591, 593]
[590, 592, 594, 596, 597, 591, 593, 595]
[590, 592, 594, 596, 597, 591, 593, 595, 598]
[1476]
[1476, 1477]
[1476, 1477, 1479]
[1476, 1477, 1479, 1481]
[1476, 1477, 1479, 1481, 1475]
[1476, 1477, 1479, 1481, 1475, 1478]
[1476, 1477, 1479, 1481, 1475, 1478, 1480]
[164]
[164, 162]
[164, 162, 163]
[1143]
[1143, 1146]
[1143, 1146, 1147]
[1143, 1146, 1147, 1144]
[1143, 1146, 1147, 1144, 1145]
[578]
[578, 579]
[578, 579, 580]
[578, 579, 580, 583]
[578, 579, 580, 583, 585]


[4946, 4948, 4949, 4950, 4951, 4953, 4954, 4945, 4947]
[4946, 4948, 4949, 4950, 4951, 4953, 4954, 4945, 4947, 4952]
[4946, 4948, 4949, 4950, 4951, 4953, 4954, 4945, 4947, 4952, 4955]
[559]
[559, 560]
[559, 560, 561]
[559, 560, 561, 563]
[559, 560, 561, 563, 565]
[559, 560, 561, 563, 565, 562]
[559, 560, 561, 563, 565, 562, 564]
[559, 560, 561, 563, 565, 562, 564, 566]
[559, 560, 561, 563, 565, 562, 564, 566, 567]
[1135]
[1135, 1136]
[1135, 1136, 1129]
[1135, 1136, 1129, 1130]
[1135, 1136, 1129, 1130, 1131]
[1135, 1136, 1129, 1130, 1131, 1132]
[1135, 1136, 1129, 1130, 1131, 1132, 1133]
[1135, 1136, 1129, 1130, 1131, 1132, 1133, 1134]
[549]
[549, 550]
[244]
[244, 245]
[244, 245, 241]
[244, 245, 241, 242]
[244, 245, 241, 242, 243]
[244, 245, 241, 242, 243, 246]
[244, 245, 241, 242, 243, 246, 247]
[244, 245, 241, 242, 243, 246, 247, 248]
[4099]
[4099, 4101]
[4099, 4101, 4103]
[4099, 4101, 4103, 4100]
[4099, 4101, 4103, 4100, 4102]
[4099, 4101, 4103, 4100, 4102, 4104]
[4099, 4101, 4103, 410

[469, 471, 472, 470]
[469, 471, 472, 470, 473]
[1179]
[1179, 1180]
[1179, 1180, 1181]
[742]
[742, 747]
[742, 747, 748]
[742, 747, 748, 749]
[742, 747, 748, 749, 752]
[742, 747, 748, 749, 752, 756]
[742, 747, 748, 749, 752, 756, 759]
[742, 747, 748, 749, 752, 756, 759, 760]
[742, 747, 748, 749, 752, 756, 759, 760, 761]
[742, 747, 748, 749, 752, 756, 759, 760, 761, 743]
[742, 747, 748, 749, 752, 756, 759, 760, 761, 743, 744]
[742, 747, 748, 749, 752, 756, 759, 760, 761, 743, 744, 745]
[742, 747, 748, 749, 752, 756, 759, 760, 761, 743, 744, 745, 746]
[742, 747, 748, 749, 752, 756, 759, 760, 761, 743, 744, 745, 746, 750]
[742, 747, 748, 749, 752, 756, 759, 760, 761, 743, 744, 745, 746, 750, 751]
[742, 747, 748, 749, 752, 756, 759, 760, 761, 743, 744, 745, 746, 750, 751, 753]
[742, 747, 748, 749, 752, 756, 759, 760, 761, 743, 744, 745, 746, 750, 751, 753, 754]
[742, 747, 748, 749, 752, 756, 759, 760, 761, 743, 744, 745, 746, 750, 751, 753, 754, 755]
[742, 747, 748, 749, 752, 756, 759, 760, 

[623, 605, 442, 353, 251, 239, 226, 220, 189, 188, 166, 160, 324, 272, 250, 250]
[623, 605, 442, 353, 251, 239, 226, 220, 189, 188, 166, 160, 324, 272, 250, 250, 186]
[623, 605, 442, 353, 251, 239, 226, 220, 189, 188, 166, 160, 324, 272, 250, 250, 186, 133]
[391]
[391, 377]
[391, 377, 364]
[391, 377, 364, 310]
[391, 377, 364, 310, 289]
[391, 377, 364, 310, 289, 284]
[391, 377, 364, 310, 289, 284, 256]
[391, 377, 364, 310, 289, 284, 256, 214]
[391, 377, 364, 310, 289, 284, 256, 214, 211]
[391, 377, 364, 310, 289, 284, 256, 214, 211, 171]
[391, 377, 364, 310, 289, 284, 256, 214, 211, 171, 122]
[391, 377, 364, 310, 289, 284, 256, 214, 211, 171, 122, 69]
[391, 377, 364, 310, 289, 284, 256, 214, 211, 171, 122, 69, 48]
[391, 377, 364, 310, 289, 284, 256, 214, 211, 171, 122, 69, 48, 433]
[391, 377, 364, 310, 289, 284, 256, 214, 211, 171, 122, 69, 48, 433, 430]
[391, 377, 364, 310, 289, 284, 256, 214, 211, 171, 122, 69, 48, 433, 430, 422]
[391, 377, 364, 310, 289, 284, 256, 214, 211, 171, 122,

In [19]:
label_dict['68832/CWE122_Heap_Based_Buffer_Overflow__cpp_CWE805_int64_t_memmove_17.cpp']

[37]

In [20]:
len(global_data)

413462

In [21]:
new_global_data = []
zero2one = 0
one2zero = 1
for p in global_data:
    dlabel, dgraph, dtarget, token_lists = p
    path = dgraph.vs['filepath'][0]
    file_key = "/".join(path.split("/")[-2:])
    if file_key not in label_dict:
        print(file_key)
        continue
    vullines = label_dict[file_key]
    new_label = 0
    for location in dgraph.vs['location']:
        if not location:
            continue
        row = int(location.split(":")[0])
        if row in vullines:
            new_label = 1
    if dlabel == 0 and new_label == 1:
        zero2one += 1
    elif dlabel == 1 and new_label == 0:
        one2zero += 1
    new_global_data.append((dlabel, new_label, dgraph, dtarget, token_lists))


149382/oids.c
149382/oids.c
102344/io.c
102344/io.c
78911/io.c
78911/io.c
62731/io.c
62731/io.c
73467/io.c
73467/io.c
72427/io.c
72427/io.c
100090/io.c
100090/io.c
114783/io.c
114783/io.c
95182/io.c
95182/io.c
85592/io.c
85592/io.c
68748/io.c
68748/io.c
116007/io.c
116007/io.c
73496/io.c
73496/io.c
78311/io.c
78311/io.c
94611/io.c
94611/io.c
149387/stream.c
149387/stream.c
149387/stream.c
149387/stream.c
149387/stream.c
149387/stream.c
149387/stream.c
149387/stream.c
68486/io.c
68486/io.c
62978/io.c
62978/io.c
63156/io.c
63156/io.c
68743/io.c
68743/io.c
76801/io.c
76801/io.c
97707/io.c
97707/io.c
65020/io.c
65020/io.c
90934/io.c
90934/io.c
115468/io.c
115468/io.c
76699/io.c
76699/io.c
964/basic-00213-med.c
73262/io.c
73262/io.c
117803/io.c
117803/io.c
97998/io.c
97998/io.c
716/basic-00151-med.c
95796/io.c
95796/io.c
71006/io.c
71006/io.c
86409/io.c
86409/io.c
91114/io.c
91114/io.c
960/basic-00212-med.c
116553/io.c
116553/io.c
71864/io.c
71864/io.c
68636/io.c
68636/io.c
91615/io.c
91615

70905/io.c
70905/io.c
80705/io.c
80705/io.c
62095/io.c
62095/io.c
114710/io.c
114710/io.c
90978/io.c
90978/io.c
88275/io.c
88275/io.c
122092/io.c
122092/io.c
81332/io.c
81332/io.c
94796/io.c
94796/io.c
107678/io.c
107678/io.c
83729/io.c
83729/io.c
69781/io.c
69781/io.c
81333/io.c
81333/io.c
97079/io.c
97079/io.c
94655/io.c
94655/io.c
83813/io.c
83813/io.c
112435/io.c
112435/io.c
102160/io.c
102160/io.c
104344/io.c
104344/io.c
68340/io.c
68340/io.c
79155/io.c
79155/io.c
116652/io.c
116652/io.c
68835/io.c
68835/io.c
115472/io.c
115472/io.c
120200/io.c
120200/io.c
96033/io.c
96033/io.c
106115/io.c
106115/io.c
665/basic-00138-min.c
67279/io.c
67279/io.c
96708/io.c
96708/io.c
79903/io.c
79903/io.c
118367/io.c
118367/io.c
91289/io.c
91289/io.c
108516/io.c
108516/io.c
71240/io.c
71240/io.c
78704/io.c
78704/io.c
88004/io.c
88004/io.c
99863/io.c
99863/io.c
85304/io.c
85304/io.c
116599/io.c
116599/io.c
81869/io.c
81869/io.c
101408/io.c
101408/io.c
101563/io.c
101563/io.c
87938/io.c
87938/io.c
11

79421/io.c
120365/io.c
120365/io.c
95697/io.c
95697/io.c
62415/io.c
62415/io.c
103798/io.c
103798/io.c
113220/io.c
113220/io.c
114559/io.c
114559/io.c
90350/io.c
90350/io.c
95351/io.c
95351/io.c
91875/io.c
91875/io.c
66996/io.c
66996/io.c
121118/io.c
121118/io.c
79965/io.c
79965/io.c
64317/io.c
64317/io.c
81946/io.c
81946/io.c
114392/io.c
114392/io.c
102561/io.c
102561/io.c
99245/io.c
99245/io.c
76897/io.c
76897/io.c
67858/io.c
67858/io.c
67912/io.c
67912/io.c
109759/io.c
109759/io.c
92378/io.c
92378/io.c
108234/io.c
108234/io.c
108235/io.c
108235/io.c
94101/io.c
94101/io.c
97864/io.c
97864/io.c
80428/io.c
80428/io.c
80241/io.c
80241/io.c
103486/io.c
103486/io.c
102486/io.c
102486/io.c
110740/io.c
110740/io.c
70102/io.c
70102/io.c
113641/io.c
113641/io.c
73634/io.c
73634/io.c
107745/io.c
107745/io.c
102566/io.c
102566/io.c
79252/io.c
79252/io.c
110417/io.c
110417/io.c
113453/io.c
113453/io.c
112515/io.c
112515/io.c
114079/io.c
114079/io.c
95624/io.c
95624/io.c
111432/io.c
111432/io.c
7

70828/io.c
120691/io.c
120691/io.c
103813/io.c
103813/io.c
70454/io.c
70454/io.c
73008/io.c
73008/io.c
113002/io.c
113002/io.c
118620/io.c
118620/io.c
89740/io.c
89740/io.c
110874/io.c
110874/io.c
118184/io.c
118184/io.c
114995/io.c
114995/io.c
110037/io.c
110037/io.c
118668/io.c
118668/io.c
75005/io.c
75005/io.c
120666/io.c
120666/io.c
104223/io.c
104223/io.c
83268/io.c
83268/io.c
69435/io.c
69435/io.c
71211/io.c
71211/io.c
65810/io.c
65810/io.c
101770/io.c
101770/io.c
74162/io.c
74162/io.c
83926/io.c
83926/io.c
69536/io.c
69536/io.c
119619/io.c
119619/io.c
110535/io.c
110535/io.c
62793/io.c
62793/io.c
95813/io.c
95813/io.c
79348/io.c
79348/io.c
96288/io.c
96288/io.c
150232/bss_file.c
150232/bss_file.c
150232/bss_file.c
150232/bss_file.c
150232/bss_file.c
150232/bss_file.c
150232/bss_file.c
113338/io.c
113338/io.c
71351/io.c
71351/io.c
74769/io.c
74769/io.c
151549/aviobuf.c
151549/aviobuf.c
151549/aviobuf.c
151549/aviobuf.c
151549/aviobuf.c
117015/io.c
117015/io.c
96265/io.c
96265/io.

117018/io.c
95332/io.c
95332/io.c
122184/io.c
122184/io.c
104121/io.c
104121/io.c
66540/io.c
66540/io.c
111648/io.c
111648/io.c
81983/io.c
81983/io.c
114059/io.c
114059/io.c
152930/main_filter_toolbar.c
152930/main_filter_toolbar.c
81980/io.c
81980/io.c
97013/io.c
97013/io.c
83018/io.c
83018/io.c
107413/io.c
107413/io.c
72323/io.c
72323/io.c
70231/io.c
70231/io.c
91811/io.c
91811/io.c
119675/io.c
119675/io.c
82066/io.c
82066/io.c
111461/io.c
111461/io.c
120748/io.c
120748/io.c
109478/io.c
109478/io.c
88453/io.c
88453/io.c
80360/io.c
80360/io.c
103231/io.c
103231/io.c
102224/io.c
102224/io.c
71199/io.c
71199/io.c
113397/io.c
113397/io.c
80367/io.c
80367/io.c
113398/io.c
113398/io.c
82143/io.c
82143/io.c
116057/io.c
116057/io.c
85510/io.c
85510/io.c
106594/io.c
106594/io.c
111346/io.c
111346/io.c
92193/io.c
92193/io.c
80560/io.c
80560/io.c
90771/io.c
90771/io.c
91885/io.c
91885/io.c
90775/io.c
90775/io.c
79089/io.c
79089/io.c
122451/io.c
122451/io.c
117058/io.c
117058/io.c
90109/io.c
901

...

64721/io.c
64721/io.c
67054/io.c
67054/io.c
76313/io.c
76313/io.c
76314/io.c
76314/io.c
101260/io.c
101260/io.c
65959/io.c
65959/io.c
88368/io.c
88368/io.c
64996/io.c
64996/io.c
120203/io.c
120203/io.c
69153/io.c
69153/io.c
115297/io.c
115297/io.c
89778/io.c
89778/io.c
115479/io.c
115479/io.c
103061/io.c
103061/io.c
114855/io.c
114855/io.c
89543/io.c
89543/io.c
91678/io.c
91678/io.c
86738/io.c
86738/io.c
62021/io.c
62021/io.c
88000/io.c
88000/io.c
79330/io.c
79330/io.c
84275/io.c
84275/io.c
80142/io.c
80142/io.c
122640/io.c
122640/io.c
81082/io.c
81082/io.c
100014/io.c
100014/io.c
103414/io.c
103414/io.c
81868/io.c
81868/io.c
79434/io.c
79434/io.c
68742/io.c
68742/io.c
101573/io.c
101573/io.c
83047/io.c
83047/io.c
73146/io.c
73146/io.c
66374/io.c
66374/io.c
62438/io.c
62438/io.c
110796/io.c
110796/io.c
83238/io.c
83238/io.c
72513/io.c
72513/io.c
111317/io.c
111317/io.c
90330/io.c
90330/io.c
91915/io.c
91915/io.c
66879/io.c
66879/io.c
89808/io.c
89808/io.c
114278/io.c
114278/io.c
67873/

77682/io.c
81121/io.c
81121/io.c
82226/io.c
82226/io.c
97010/io.c
97010/io.c
107071/io.c
107071/io.c
98765/io.c
98765/io.c
77448/io.c
77448/io.c
88250/io.c
88250/io.c
100841/io.c
100841/io.c
110868/io.c
110868/io.c
71506/io.c
71506/io.c
69494/io.c
69494/io.c
100846/io.c
100846/io.c
89679/io.c
89679/io.c
68488/io.c
68488/io.c
120722/io.c
120722/io.c
76936/io.c
76936/io.c
69551/io.c
69551/io.c
83013/io.c
83013/io.c
83011/io.c
83011/io.c
107494/io.c
107494/io.c
72088/io.c
72088/io.c
64512/io.c
64512/io.c
66387/io.c
66387/io.c
119997/io.c
119997/io.c
67702/io.c
67702/io.c
97902/io.c
97902/io.c
69069/io.c
69069/io.c
74244/io.c
74244/io.c
61998/io.c
61998/io.c
88710/io.c
88710/io.c
64680/io.c
64680/io.c
94330/io.c
94330/io.c
92763/io.c
92763/io.c
67383/io.c
67383/io.c
114858/io.c
114858/io.c
86498/io.c
86498/io.c
62123/io.c
62123/io.c
111804/io.c
111804/io.c
66251/io.c
66251/io.c
119517/io.c
119517/io.c
80202/io.c
80202/io.c
66256/io.c
66256/io.c
96656/io.c
96656/io.c
112776/io.c
112776/io.c

89803/io.c
110793/io.c
110793/io.c
64279/io.c
64279/io.c
111315/io.c
111315/io.c
69674/io.c
69674/io.c
96826/io.c
96826/io.c
115888/io.c
115888/io.c
99380/io.c
99380/io.c
67872/io.c
67872/io.c
99384/io.c
99384/io.c
116097/io.c
116097/io.c
102699/io.c
102699/io.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
152486/portalmem.c
116159/io.c
116159/io.c
121874/io.c
121874/io.c
109745/io.c
109745/io.c
97854/io.c
97854/io.c
102505/io.c
102505/io.c
73258/io.c
73258/io.c
87745/io.c
87745/io.c
104166/io.c
104166/io.c
101316/io.c
101316/io.c
106049/io.c
106049/io.c
115277/io.c
115277/io.c
7626

72515/io.c
78928/io.c
78928/io.c
77401/io.c
77401/io.c
81575/io.c
81575/io.c
102033/io.c
102033/io.c
81578/io.c
81578/io.c
89904/io.c
89904/io.c
117743/io.c
117743/io.c
119702/io.c
119702/io.c
63368/io.c
63368/io.c
82606/io.c
82606/io.c
80338/io.c
80338/io.c
83909/io.c
83909/io.c
107499/io.c
107499/io.c
106623/io.c
106623/io.c
95778/io.c
95778/io.c
83902/io.c
83902/io.c
69459/io.c
69459/io.c
80987/io.c
80987/io.c
120648/io.c
120648/io.c
112650/io.c
112650/io.c
71237/io.c
71237/io.c
81867/io.c
81867/io.c
110917/io.c
110917/io.c
120961/io.c
120961/io.c
64380/io.c
64380/io.c
108430/io.c
108430/io.c
83293/io.c
83293/io.c
117089/io.c
117089/io.c
69330/io.c
69330/io.c
111849/io.c
111849/io.c
121996/io.c
121996/io.c
68914/io.c
68914/io.c
108987/io.c
108987/io.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact.c
151920/xact

150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/shm_setup.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
150894/shm_setup.c
150894/e_camellia.c
150894/shm_setup.c
150894/shm_setup.c
150894/e_camellia.c
150894/e_camellia.c
150894/e_camellia.c
98635/io.c
98635/io.c
68184/io.c
68184/io.c
73484/io.c
73484/io.c
71176/io.c
71176/io.c
98399/io.c
98399/io.c
78523/io.c
78523/io.c
106664/io.c
106664/io.c
118563/io.c
118563/io.c
117986/io.c
117986/io.c
65248/io.c
65248/io.c
71997/io.c
71997/io.c
119088/io.c
119088/io.c
116568/io.c
116568/io.c
95149/io.c
95149/io.c
63009/io.c
63009/io.c
91168/io.c
91168/io.c
72892/io.c
72892/io.c
70913/io.c
70913/io.c
101173/io.c
101173/io.c
114464/io.c
114464/io.c
119778/io.

In [22]:
del global_data

In [ ]:
zero_cnt = 0
one_cnt = 0
skip_cnt = 0
for p in new_global_data:
    dlabel, new_label, dgraph, dtarget, token_lists = p
    if dlabel == 1 and new_label == 0:
        skip_cnt += 1
        if skip_cnt == 2:
            break
    if new_label == 0:
        zero_cnt += 1
    else:
        one_cnt += 1


In [ ]:
dgraph.vs['location']

In [ ]:
dgraph.vs['code']

In [ ]:
print(dgraph.vs['filepath'])

print(dtarget)

In [ ]:
zero_cnt

In [ ]:
one_cnt

In [ ]:
zero2one

In [ ]:
one2zero

In [25]:
import torch
import random
import numpy as np
from torch_geometric.data import Data
mask_pool = [0,0,0,0,0,0,0,1,2,2] # 0: train, 1: valid, 2: test

In [98]:
data_list = []
for i in range(len(new_global_data)):
    print("\r# processing {}/{}".format(len(data_list), len(new_global_data)), end="")
    old_label, dlabel, dgraph, dtarget, token_lists = new_global_data[i]
    dtarget_index = dgraph.vs["name"].index(dtarget)
    # construct edge matrix
    edge_index_from = []
    edge_index_to = []
    for q in dgraph.es:
        edge_index_from.append(q.source)
        edge_index_to.append(q.target)
    # construct feature matrix (x)
    feature_x = []
    for token_list in token_lists:
        tmp_s = token_list + ["<PAD>" for _ in range(MAX_CODE_LEN)]
        tmp_i = []
        for token in tmp_s[:MAX_CODE_LEN]:
            if token in token_dict:
                tmp_i.extend(list(model.wv[token]))
            else:
                tmp_i.extend([0.0] * SIZE)
            # token_dict[r] if r in token_dict.keys() else token_dict["<UNK>"]
            # for r in tmp_s[:MAX_CODE_LEN]
        feature_x.append(tmp_i)
    # construct mask
    # only include the target node, others will be masked out for all mask types
    mtype = random.choice(mask_pool)
    train_mask = [False for _ in range(len(dgraph.vs))]
    val_mask = [False for _ in range(len(dgraph.vs))]
    test_mask = [False for _ in range(len(dgraph.vs))]
    # literally all nodes from one graph follows the label of the target node
    label_y = [1 if dlabel else 0 for _ in range(len(dgraph.vs))]
    if mtype==0:
        # train
        train_mask[dtarget_index] = True
    elif mtype==1:
        # valid
        val_mask[dtarget_index] = True
    elif mtype==2:
        # test
        test_mask[dtarget_index] = True
    else:
        # how did you get here?
        raise Exception("How did you get here?")
    # then construct Data
    tmp_data = Data(
        # x=torch.tensor(feature_x, dtype=torch.long),
        x=torch.tensor(feature_x, dtype=torch.float),
        y=torch.tensor(label_y, dtype=torch.long),
        edge_index=torch.tensor([edge_index_from, edge_index_to], dtype=torch.long),
        train_mask=torch.tensor(train_mask, dtype=torch.bool),
        val_mask=torch.tensor(val_mask, dtype=torch.bool),
        test_mask=torch.tensor(test_mask, dtype=torch.bool),
        global_index=torch.tensor(i, dtype=torch.long)
    )
    data_list.append(tmp_data)

# processing 233812/233813

In [101]:
data_list

[Data(edge_index=[2, 21], global_index=0, test_mask=[10], train_mask=[10], val_mask=[10], x=[10, 1920], y=[10]),
 Data(edge_index=[2, 18], global_index=1, test_mask=[9], train_mask=[9], val_mask=[9], x=[9, 1920], y=[9]),
 Data(edge_index=[2, 9], global_index=2, test_mask=[6], train_mask=[6], val_mask=[6], x=[6, 1920], y=[6]),
 Data(edge_index=[2, 21], global_index=3, test_mask=[10], train_mask=[10], val_mask=[10], x=[10, 1920], y=[10]),
 Data(edge_index=[2, 18], global_index=4, test_mask=[9], train_mask=[9], val_mask=[9], x=[9, 1920], y=[9]),
 Data(edge_index=[2, 9], global_index=5, test_mask=[6], train_mask=[6], val_mask=[6], x=[6, 1920], y=[6]),
 Data(edge_index=[2, 21], global_index=6, test_mask=[10], train_mask=[10], val_mask=[10], x=[10, 1920], y=[10]),
 Data(edge_index=[2, 18], global_index=7, test_mask=[9], train_mask=[9], val_mask=[9], x=[9, 1920], y=[9]),
 Data(edge_index=[2, 9], global_index=8, test_mask=[6], train_mask=[6], val_mask=[6], x=[6, 1920], y=[6]),
 Data(edge_index

In [100]:
with open("SySeVR_GraphDataset_token_unk_w2v_16_new_label_concat_with_index.pkl", "wb") as writer:
    pickle.dump(data_list, writer)

# Error Analysis

## Old / New Label diff

In [83]:
old_label = []
new_label = []
for p in new_global_data:
    old, new, _, _, _ = p
    old_label.append(old)
    new_label.append(new)
y_actu = pd.Series(old_label, name='old_label')
y_pred = pd.Series(new_label, name='new_label')
df_confusion = pd.crosstab(y_actu, y_pred)

In [84]:
df_confusion

new_label       0      1
old_label               
False      162022   9519
True        45690  16582

## Error Analysis of Model

In [40]:
import pickle
with open("logit_pred.pkl", "rb") as reader:
    pred = pickle.load(reader)

In [95]:
train_label = []
for data in data_list:
    train_label.append(int(data.y[0]))

In [550]:
index = 35651

In [551]:
display(new_global_data[index][0], new_global_data[index][1])

False

0

In [552]:
display(new_global_data[index][2].vs['filepath'][0])
display([" ".join(x) for x in new_global_data[index][4]])

'/opt/ReSySeVR/data/SARD/dir_011/72809/CWE122_Heap_Based_Buffer_Overflow__c_dest_char_cat_10.c'

['char variable_0 [ 100 ] ;',
 'strcat ( variable_1 , variable_0 )',
 "variable_0 [ 100 - 1 ] = ' \\ 0 '",
 "memset ( variable_0 , ' C ' , 100 - 1 )",
 'variable_1 = ( char * ) malloc ( 100 * sizeof ( char ) )',
 "variable_1 [ 0 ] = ' \\ 0 '",
 'variable_1 = NULL',
 'variable_2',
 'variable_3',
 'char * variable_1 ;']

In [553]:
new_global_data[index][3]

'851607'

In [554]:
new_global_data[index][2].vs['name']

['851637',
 '851607',
 '851616',
 '851624',
 '851650',
 '851644',
 '851667',
 '851665',
 '851587',
 '851671']

In [555]:
new_global_data[index][2].vs['code']

['char source [ 100 ] ;',
 'strcat ( data , source )',
 "source [ 100 - 1 ] = '\\0'",
 "memset ( source , 'C' , 100 - 1 )",
 'data = ( char * ) malloc ( 100 * sizeof ( char ) )',
 "data [ 0 ] = '\\0'",
 'data = NULL',
 'globalTrue',
 'goodG2B2',
 'char * data ;']

In [556]:
new_global_data[index][2].vs['location']

['87:8:2714:2730',
 '91:8:2958:2978',
 '89:8:2799:2819',
 '88:8:2741:2767',
 '83:8:2604:2643',
 '84:8:2654:2668',
 '79:4:2430:2441',
 '80:7:2451:2460',
 '76:0:2381:3035',
 '78:4:2412:2423']